In [13]:
import pandas as pd
import plotly as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.graph_objects as go
from scipy.stats import kendalltau, pearsonr
from sklearn.metrics import roc_curve, auc, roc_auc_score

import numpy as np

In [38]:
def sample_human_equivalent_participant(data: pd.DataFrame, participants: pd.DataFrame, gender: str, num_humans: int = 2):
    sampled = []
    for part in range(1,5):
        sampled.append(participants[(participants['gender'] == gender) & (participants['part'] == part)].sample(num_humans)['participants'])
    person1 = data.loc[data['subject.id'].isin([s.iloc[0] for s in sampled])]
    person1.loc[:, 'human1_dist'] = 6 - person1['keyPressed']
    person1=person1.set_index(['img_1', 'img_2'])
    person1=person1[['human1_dist', 'isSame']]
    
    person2 = data.loc[data['subject.id'].isin([s.iloc[1] for s in sampled])]
    person2=person2.set_index(['img_1', 'img_2'])
    person2.loc[:, 'human2_dist'] = 6 - person2['keyPressed']
    person2=person2[['human2_dist', 'isSame']]
    
    joined = person1.join(person2, how='inner', lsuffix='_l', rsuffix='_r')
    joined.loc[:, 'isSame'] = joined['isSame_l'] & joined['isSame_r']
    joined = joined.reset_index()
    return joined

def load_nn_pairs(nn_path, nn_label):
    nn_matrix = pd.read_csv(nn_path)
    nn_matrix = nn_matrix.rename(columns={'Unnamed: 0': 'img_1'})
    nn_pairs = nn_matrix.melt(id_vars=['img_1'], var_name='img_2', value_name=nn_label)
    return nn_pairs.set_index(['img_1', 'img_2'])

def load_all_data(nn1_path: str, 
                  nn1_label: str, 
                  nn2_path: str, 
                  nn2_label: str, 
                  participants_path: str, participants_data_path: str, gender: str):
    nn1_pairs = load_nn_pairs(nn1_path, nn1_label)
    nn2_pairs = load_nn_pairs(nn2_path, nn2_label)
    
    participants = pd.read_csv(participants_path)
    data = pd.read_csv(participants_data_path)
    data.loc[:,'img_1'] = data.apply(lambda row: row['img_1'].replace(' ', '_'), axis=1)
    data.loc[:,'img_2'] = data.apply(lambda row: row['img_2'].replace(' ', '_'), axis=1)
    human_eq = sample_human_equivalent_participant(data, participants, gender)
    
    joined = human_eq.join(nn1_pairs, how='inner', on=['img_1', 'img_2'])
    joined = joined.join(nn2_pairs, how='inner', on=['img_1', 'img_2'])
    
    joined = joined.drop(joined[joined['img_1'] == joined['img_2']].index)
    return joined

def calc_graph_measurements(df: pd.DataFrame, label_col: str, value_col: str):
    fpr, tpr, thresh = roc_curve(df[label_col], df[value_col], pos_label=0)
    roc_auc = auc(fpr, tpr)
        
    return fpr, tpr, thresh, roc_auc


In [39]:
participants = pd.read_csv('/home/administrator/datasets/itays_exp_human_measurements/participants.csv')
measures = pd.read_csv('/home/administrator/datasets/itays_exp_human_measurements/females_raw_data.csv')
measures['isSame'] & measures['isSame']

0        0
1        0
2        0
3        0
4        0
        ..
27775    0
27776    1
27777    0
27778    0
27779    0
Name: isSame, Length: 27780, dtype: int64

In [40]:
nn1_path='/home/administrator/Downloads/female_l2_not_normed_images_distance_matrix_2021_10_05_12_07_38_219932.csv'
nn2_path='/home/administrator/experiments/high_importance_features_full_dataset/vgg16/results/female/fc7.csv'
participants_path = '/home/administrator/datasets/itays_exp_human_measurements/participants.csv'
participants_data_path = '/home/administrator/datasets/itays_exp_human_measurements/females_raw_data.csv'

f_joined = load_all_data(nn1_path, 'CLIP', nn2_path, 'vgg16', participants_path, participants_data_path, 'f')
f_joined = f_joined[['img_1', 'img_2', 'human1_dist', 'human2_dist', 'CLIP', 'vgg16', 'isSame']]
f_joined.to_csv('/home/ssd_storage/experiments/CLIP-vgg-Human comparison/female_comparison.csv')

nn1_path='/home/administrator/Downloads/male_l2_not_normed_images_distance_matrix_2021_10_05_12_09_07_849568.csv'
nn2_path='/home/administrator/experiments/high_importance_features_full_dataset/vgg16/results/male/fc7.csv'
participants_path = '/home/administrator/datasets/itays_exp_human_measurements/participants.csv'
participants_data_path = '/home/administrator/datasets/itays_exp_human_measurements/males_raw_data.csv'

m_joined = load_all_data(nn1_path, 'CLIP', nn2_path, 'vgg16', participants_path, participants_data_path, 'm')
m_joined = m_joined[['img_1', 'img_2', 'human1_dist', 'human2_dist', 'CLIP', 'vgg16', 'isSame']]
m_joined.to_csv('/home/ssd_storage/experiments/CLIP-vgg-Human comparison/male_comparison.csv')

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is tryin

In [41]:
nn1_path='/home/administrator/Downloads/female_l2_not_normed_images_distance_matrix_2021_10_05_12_07_38_219932.csv'
nn2_path='/home/administrator/experiments/high_importance_features_full_dataset/vgg16/results/female/fc7.csv'
participants_path = '/home/administrator/datasets/itays_exp_human_measurements/participants.csv'
participants_data_path = '/home/administrator/datasets/itays_exp_human_measurements/females_raw_data.csv'


joined = load_all_data(nn1_path, 'CLIP', nn2_path, 'vgg16', participants_path, participants_data_path, 'f')

print(pearsonr(joined['CLIP'], joined['vgg16']))

CLIP_vgg_ktau = kendalltau(joined['CLIP'], joined['vgg16'])
human_vgg_ktau = kendalltau(joined['human1_dist'], joined['vgg16'])
CLIP_human_ktau = kendalltau(joined['human1_dist'], joined['CLIP'])
# human2_vgg_ktau = kendalltau(joined['human2_dist'], joined['vgg16'])
# CLIP_human2_ktau = kendalltau(joined['human2_dist'], joined['CLIP'])
# human1_human2_ktau = kendalltau(joined['human1_dist'], joined['human2_dist'])

title = f'clip-vgg = {CLIP_vgg_ktau}\n human-vgg = {human_vgg_ktau}\n CLIP_human_ktau = {CLIP_human_ktau}'
fig = go.Figure()
fig.add_shape(
    type='line', line=dict(dash='dash'),
    x0=0, x1=1, y0=0, y1=1
)

fpr, tpr, thresh, roc_auc = calc_graph_measurements(joined, 'isSame', 'human1_dist')

name = f"Human (1) equivalent (AUC={roc_auc:.2f})"
fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines'))

fpr, tpr, thresh, roc_auc = calc_graph_measurements(joined, 'isSame', 'human2_dist')

name = f"Human (1) equivalent (AUC={roc_auc:.2f})"
fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines'))

fpr, tpr, thresh, roc_auc = calc_graph_measurements(joined, 'isSame', 'CLIP')

name = f"CLIP (AUC={roc_auc:.2f})"
fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines'))

fpr, tpr, thresh, roc_auc = calc_graph_measurements(joined, 'isSame', 'vgg16')

name = f"vgg16 (AUC={roc_auc:.2f})"
fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines'))


fig.update_layout(
    title=f'female',
    xaxis_title='False Positive Rate',
    yaxis_title='True Positive Rate',
    yaxis=dict(scaleanchor="x", scaleratio=1),
    xaxis=dict(constrain='domain'),
    width=700, height=500,
)
fig.show()
fig.write_html('/home/administrator/Downloads/female_vgg-clip-human_roc.html')
print(title)

(0.3405003183092176, 1.0314103227614459e-64)


/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



clip-vgg = KendalltauResult(correlation=0.20039868958294185, pvalue=6.511325661807688e-48)
 human-vgg = KendalltauResult(correlation=0.22551390284999356, pvalue=1.9953701202786952e-48)
 CLIP_human_ktau = KendalltauResult(correlation=0.1659687641524342, pvalue=5.195888331266053e-27)


In [42]:
from sklearn import linear_model, metrics
from sklearn.model_selection import train_test_split

train, test = train_test_split(joined, test_size=0.3)

X_train = train[['CLIP', 'vgg16']]
y_train = train['human1_dist']
X_test = test[['CLIP', 'vgg16']]
y_test = test['human1_dist']


regr = linear_model.LinearRegression()
regr.fit(X_train, y_train)
print(f"coefficients: {regr.coef_}")
print(f"test accuracy: {metrics.mean_squared_error(y_test, regr.predict(X_test))}")
print(f"train accuracy: {metrics.mean_squared_error(y_train, regr.predict(X_train))}")

print('full_regr')
full_regr = linear_model.LinearRegression()
X = joined[['CLIP', 'vgg16']]
y = joined['human1_dist']
full_regr.fit(X, y)
print(f"coefficients: {full_regr.coef_}")
print(f"test accuracy: {metrics.mean_squared_error(y, full_regr.predict(X))}")




coefficients: [2.82844785 0.01322894]
test accuracy: 1.7885163038193623
train accuracy: 1.876668442612597
full_regr
coefficients: [2.93532758 0.01362919]
test accuracy: 1.849807633869407


In [43]:
nn1_path='/home/administrator/Downloads/male_l2_not_normed_images_distance_matrix_2021_10_05_12_09_07_849568.csv'
nn2_path='/home/administrator/experiments/high_importance_features_full_dataset/vgg16/results/male/fc7.csv'
participants_path = '/home/administrator/datasets/itays_exp_human_measurements/participants.csv'
participants_data_path = '/home/administrator/datasets/itays_exp_human_measurements/males_raw_data.csv'

joined = load_all_data(nn1_path, 'CLIP', nn2_path, 'vgg16', participants_path, participants_data_path, 'm')



/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [44]:
def get_same_dist(joined: pd.DataFrame, col: str):
    zero_val = pd.DataFrame(joined['img_1'].unique())
    zero_val = zero_val.append(pd.DataFrame(joined['img_2'].unique()))
    zero_val = pd.DataFrame(zero_val[0].unique(), columns=['img_1'])
    zero_val['img_2'] = zero_val['img_1']
    zero_val[col] = 0
    return zero_val

def get_rdm(joined: pd.DataFrame, col: str):
    joined = joined.append(get_same_dist(joined, col))
    filtered = joined[['img_1', 'img_2', col]]
    filtered = filtered.sort_values(['img_1', 'img_2'])
    filtered = filtered.pivot_table(index='img_1', columns='img_2')
    
    return filtered

def fix_symmetry(rdm: pd.DataFrame):
    rdm_np = rdm.fillna(0).to_numpy() # setting NaNs as 0
    filled_nans = rdm_np + rdm_np.T * rdm.isna() # mask for only NaNs
    upper_tri = np.triu(filled_nans, k=0)
    return pd.DataFrame(upper_tri + upper_tri.T, index=rdm.index, columns=rdm.columns)


In [45]:
def df_to_plotly(df):
    np_vals = np.array(df.values.tolist())
    normalized = (np_vals - np_vals.min()) / (np_vals.max() - np_vals.min())

    return {'z': normalized}
#             'x': [col[1] for col in df.columns.tolist()],
#             'y': df.index.tolist()}

# fig = go.Figure(data=go.Heatmap(df_to_plotly(df)))
# fig.update_layout(width=700, height=700, title='Human - male RDM')
# fig['layout']['xaxis']['autorange'] = "reversed"
# fig.show()



fig = make_subplots(
rows=2, cols=4, shared_xaxes=True, 
vertical_spacing=0.02,
# column_widths=3*[250], row_heights=2*[100], 
    column_titles=['human1', 'human2', 'CLIP', 'vgg16'],
    row_titles=['female','male'])

# nn1_path='/home/administrator/Downloads/female_l2_not_normed_images_distance_matrix_2021_10_05_12_07_38_219932.csv'
nn1_path='/home/administrator/Downloads/female_rn50x16_images_distance_matrix_2021_10_07_13_07_12_087880.csv'
nn2_path='/home/administrator/experiments/high_importance_features_full_dataset/vgg16/results/female/fc7.csv'
participants_path = '/home/administrator/datasets/itays_exp_human_measurements/participants.csv'
participants_data_path = '/home/administrator/datasets/itays_exp_human_measurements/females_raw_data.csv'
female = load_all_data(nn1_path, 'CLIP', nn2_path, 'vgg16', participants_path, participants_data_path, 'f')

df = fix_symmetry(get_rdm(female, 'human1_dist'))
fig.add_trace(go.Heatmap(df_to_plotly(df)),
          row=1, col=1)
df = fix_symmetry(get_rdm(female, 'human2_dist'))
fig.add_trace(go.Heatmap(df_to_plotly(df)),
          row=1, col=2)
df = fix_symmetry(get_rdm(female, 'CLIP'))

fig.add_trace(go.Heatmap(df_to_plotly(df)),
          row=1, col=3)
df = fix_symmetry(get_rdm(female, 'vgg16'))
fig.add_trace(go.Heatmap(df_to_plotly(df)),
          row=1, col=4)

# nn1_path='/home/administrator/Downloads/male_l2_not_normed_images_distance_matrix_2021_10_05_12_09_07_849568.csv'
nn1_path='/home/administrator/Downloads/male_rn50x16_images_distance_matrix_2021_10_07_13_09_24_712292.csv'
nn2_path='/home/administrator/experiments/high_importance_features_full_dataset/vgg16/results/male/fc7.csv'
participants_path = '/home/administrator/datasets/itays_exp_human_measurements/participants.csv'
participants_data_path = '/home/administrator/datasets/itays_exp_human_measurements/males_raw_data.csv'
male = load_all_data(nn1_path, 'CLIP', nn2_path, 'vgg16', participants_path, participants_data_path, 'm')

figg = go.Figure()
figg.add_trace(go.Heatmap(df_to_plotly(get_rdm(male, 'CLIP').fillna(0))))
figg.show()

df = fix_symmetry(get_rdm(male, 'human1_dist'))
fig.add_trace(go.Heatmap(df_to_plotly(df)),
          row=2, col=1)
df = fix_symmetry(get_rdm(male, 'human2_dist'))
fig.add_trace(go.Heatmap(df_to_plotly(df)),
          row=2, col=2)
df = fix_symmetry(get_rdm(male, 'CLIP'))
fig.add_trace(go.Heatmap(df_to_plotly(df)),
          row=2, col=3)
df = fix_symmetry(get_rdm(male, 'vgg16'))
fig.add_trace(go.Heatmap(df_to_plotly(df)),
          row=2, col=4)

fig.update_xaxes(row=1, col=1, autorange='reversed')
fig.update_xaxes(row=1, col=2, autorange='reversed')
fig.update_xaxes(row=1, col=3, autorange='reversed')
fig.update_xaxes(row=1, col=4, autorange='reversed')
fig.update_xaxes(row=2, col=1, autorange='reversed')
fig.update_xaxes(row=2, col=2, autorange='reversed')
fig.update_xaxes(row=2, col=3, autorange='reversed')
fig.update_xaxes(row=1, col=4, autorange='reversed')
fig.update_layout(height=600, width=1200)

fig.show()
fig.write_html('/home/ssd_storage/experiments/CLIP-vgg-Human comparison/rn50x16_RDMs.html')

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is tryin

In [46]:
def ROC(df: pd.DataFrame, gender: str):
    CLIP_vgg_ktau = kendalltau(df['CLIP'], df['vgg16'])
    human_vgg_ktau = kendalltau(df['human_dist'], df['vgg16'])
    CLIP_human_ktau = kendalltau(df['human_dist'], df['CLIP'])

    title = f'clip-vgg = {CLIP_vgg_ktau}\n human-vgg = {human_vgg_ktau}\n CLIP_human_ktau = {CLIP_human_ktau}'
    fig = go.Figure()
    fig.add_shape(
        type='line', line=dict(dash='dash'),
        x0=0, x1=1, y0=0, y1=1
    )

    fpr, tpr, thresh, roc_auc = calc_graph_measurements(df, 'isSame', 'human_dist')

    name = f"Human equivalent (AUC={roc_auc:.2f})"
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines'))

    fpr, tpr, thresh, roc_auc = calc_graph_measurements(df, 'isSame', 'CLIP')

    name = f"CLIP (AUC={roc_auc:.2f})"
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines'))

    fpr, tpr, thresh, roc_auc = calc_graph_measurements(df, 'isSame', 'vgg16')

    name = f"vgg16 (AUC={roc_auc:.2f})"
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines'))


    fig.update_layout(
        title=gender,
        xaxis_title='False Positive Rate',
        yaxis_title='True Positive Rate',
        yaxis=dict(scaleanchor="x", scaleratio=1),
        xaxis=dict(constrain='domain'),
        width=700, height=500
    )
    fig.show()
    fig.write_html('/home/ssd_storage/experiments/CLIP-vgg-Human comparison/{gender}_vgg-clip(rn50x16)-human_roc.html.html')
#     fig.write_html(f'/home/administrator/Downloads/{gender}_vgg-clip-human_roc.html')
    print(title)

In [47]:
joined.sort_values(['img_1', 'img_2'])


img_1        img_2  human1_dist  isSame_l  human2_dist  isSame_r  \
1286   CL_(1).jpg  CL_(10).jpg            1         1            3         1   
105    CL_(1).jpg  CL_(18).jpg            0         1            0         1   
194    CL_(1).jpg  CL_(21).jpg            2         1            4         1   
1579   CL_(1).jpg  CL_(22).jpg            3         1            5         1   
2699   CL_(1).jpg  CL_(23).jpg            4         1            0         1   
...           ...          ...          ...       ...          ...       ...   
6      SA_(4).jpg  SA_(45).jpg            2         1            0         1   
631    SA_(4).jpg   SA_(8).jpg            1         1            1         1   
1358  SA_(45).jpg  SA_(43).jpg            0         1            2         1   
883   SA_(45).jpg   SA_(8).jpg            0         1            2         1   
2221   SA_(8).jpg  SA_(43).jpg            5         1            2         1   

      isSame      CLIP      vgg16  
1286       1  0.640851  127.07672  
105        1  0.753444  190.42140  
194        1  0.644960  169.85889  
1579       1  0.636856  193.61343  
2699       1  0.676155  140.84651  
...      ...       ...        ...  
6          1  0.675384  208.49069  
631        1  0.421070  140.41052  
1358       1  0.678340  196.52045  
883        1  0.643698  201.43683  
2221       1  0.774704  242.81822  

[2410 rows x 9 columns]

In [52]:
import numpy as np

def acc(df: pd.DataFrame, val_col: str, label_col: str):
#     label = df[label_col] * 2 - 1
    best_acc = 0
    for val in df[val_col]:
        curr_acc = np.mean(((df[val_col] < val) == df[label_col]) > 0)
        best_acc = max(curr_acc, best_acc)
    return best_acc

print(acc(female, 'CLIP', 'isSame'))
print(acc(male, 'CLIP', 'isSame'))
print(acc(pd.concat([female, male]), 'CLIP', 'isSame'))

0.8489761092150171
0.8688796680497926
0.8584350021034918


In [647]:
def multi_ROC(male: pd.DataFrame, female:pd.DataFrame):
    CLIP_vgg_ktau = kendalltau(male['CLIP'], male['vgg16'])
    human1_vgg_ktau = kendalltau(male['human1_dist'], male['vgg16'])
    CLIP_human1_ktau = kendalltau(male['human1_dist'], male['CLIP'])
    human2_vgg_ktau = kendalltau(male['human2_dist'], male['vgg16'])
    CLIP_human2_ktau = kendalltau(male['human2_dist'], male['CLIP'])
    human1_human2_ktau = kendalltau(male['human1_dist'], male['human2_dist'])
    
    title = f'male clip-vgg = {CLIP_vgg_ktau}\nhuman1-vgg = {human1_vgg_ktau}\nCLIP-human1 = {CLIP_human1_ktau}\nhuman2-vgg = {human2_vgg_ktau}\nCLIP-human2 = {CLIP_human2_ktau}\nhuman1-human2 = {human1_human2_ktau}\n'
    print(title)
    
    CLIP_vgg_ktau = kendalltau(female['CLIP'], female['vgg16'])
    human1_vgg_ktau = kendalltau(female['human1_dist'], female['vgg16'])
    CLIP_human1_ktau = kendalltau(female['human1_dist'], female['CLIP'])
    human2_vgg_ktau = kendalltau(female['human2_dist'], female['vgg16'])
    CLIP_human2_ktau = kendalltau(female['human2_dist'], female['CLIP'])
    human1_human2_ktau = kendalltau(female['human1_dist'], female['human2_dist'])
    
    title = f'female clip-vgg = {CLIP_vgg_ktau}\nhuman1-vgg = {human1_vgg_ktau}\nCLIP-human1 = {CLIP_human1_ktau}\nhuman2-vgg = {human2_vgg_ktau}\nCLIP-human2 = {CLIP_human2_ktau}\nhuman1-human2 = {human1_human2_ktau}\n'
    print(title)

    
    fig = make_subplots(
        rows=1, cols=2, shared_xaxes=True, 
        vertical_spacing=0.02,
        # column_widths=3*[250], row_heights=2*[100], 
        column_titles=['female', 'male'])
    fig.add_shape(
        row=1, col=1,
        type='line', line=dict(dash='dash'),
        x0=0, x1=1, y0=0, y1=1
    )
    fig.add_shape(
        row=1, col=2,
        type='line', line=dict(dash='dash'),
        x0=0, x1=1, y0=0, y1=1
    )

    fpr, tpr, thresh, roc_auc = calc_graph_measurements(female, 'isSame', 'human1_dist')

    name = f"Human (1) equivalent (AUC={roc_auc:.2f})"
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines', marker_color=px.colors.qualitative.Plotly[0]), row=1, col=1)
    
    fpr, tpr, thresh, roc_auc = calc_graph_measurements(female, 'isSame', 'human2_dist')

    name = f"Human (2) equivalent (AUC={roc_auc:.2f})"
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines', marker_color=px.colors.qualitative.Plotly[3]), row=1, col=1)

    fpr, tpr, thresh, roc_auc = calc_graph_measurements(female, 'isSame', 'CLIP')

    name = f"CLIP (AUC={roc_auc:.2f})"
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines', marker_color=px.colors.qualitative.Plotly[1]), row=1, col=1)

    fpr, tpr, thresh, roc_auc = calc_graph_measurements(female, 'isSame', 'vgg16')

    name = f"vgg16 (AUC={roc_auc:.2f})"
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines', marker_color=px.colors.qualitative.Plotly[2]), row=1, col=1)
    
    fpr, tpr, thresh, roc_auc = calc_graph_measurements(male, 'isSame', 'human1_dist')

    name = f"Human (1) equivalent (AUC={roc_auc:.2f})"
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines', marker_color=px.colors.qualitative.Plotly[0]), row=1, col=2)
    
    fpr, tpr, thresh, roc_auc = calc_graph_measurements(male, 'isSame', 'human2_dist')
    
    name = f"Human (2) equivalent (AUC={roc_auc:.2f})"
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines', marker_color=px.colors.qualitative.Plotly[3]), row=1, col=2)

    fpr, tpr, thresh, roc_auc = calc_graph_measurements(male, 'isSame', 'CLIP')

    name = f"CLIP (AUC={roc_auc:.2f})"
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines', marker_color=px.colors.qualitative.Plotly[1]), row=1, col=2)

    fpr, tpr, thresh, roc_auc = calc_graph_measurements(male, 'isSame', 'vgg16')

    name = f"vgg16 (AUC={roc_auc:.2f})"
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines', marker_color=px.colors.qualitative.Plotly[2]), row=1, col=2)


    fig.update_layout(
        title=gender,
        xaxis_title='False Positive Rate',
        yaxis_title='True Positive Rate',
        yaxis=dict(scaleanchor="x", scaleratio=1),
        xaxis=dict(constrain='domain'),
        width=1000, height=500,
    )
    fig.update_xaxes(row=1)
    fig.show()
    fig.write_html('/home/ssd_storage/experiments/CLIP-vgg-Human comparison/vgg-clip(rn50x16)-human_roc.html.html')
#     fig.write_html(f'/home/administrator/Downloads/vgg-clip-human_roc.html')
    print(title)

In [648]:


multi_ROC(male,female)

male clip-vgg = KendalltauResult(correlation=0.3458515916043458, pvalue=3.684815296013332e-143)
human1-vgg = KendalltauResult(correlation=0.3511528691008326, pvalue=2.680821551129859e-112)
CLIP-human1 = KendalltauResult(correlation=0.33713573490959975, pvalue=1.1530972618602646e-103)
human2-vgg = KendalltauResult(correlation=0.3342593647095006, pvalue=1.858133964424632e-102)
CLIP-human2 = KendalltauResult(correlation=0.3340354964265451, pvalue=2.5332145865590955e-102)
human1-human2 = KendalltauResult(correlation=0.439398853899101, pvalue=1.4185728252708177e-133)

female clip-vgg = KendalltauResult(correlation=0.23251271676721222, pvalue=6.686850236207598e-64)
human1-vgg = KendalltauResult(correlation=0.3229683009762027, pvalue=2.1757453856343556e-95)
CLIP-human1 = KendalltauResult(correlation=0.21075025023246763, pvalue=1.1562238370455905e-41)
human2-vgg = KendalltauResult(correlation=0.256762715197011, pvalue=8.107637838377612e-62)
CLIP-human2 = KendalltauResult(correlation=0.18503989

female clip-vgg = KendalltauResult(correlation=0.23251271676721222, pvalue=6.686850236207598e-64)
human1-vgg = KendalltauResult(correlation=0.3229683009762027, pvalue=2.1757453856343556e-95)
CLIP-human1 = KendalltauResult(correlation=0.21075025023246763, pvalue=1.1562238370455905e-41)
human2-vgg = KendalltauResult(correlation=0.256762715197011, pvalue=8.107637838377612e-62)
CLIP-human2 = KendalltauResult(correlation=0.18503989294180254, pvalue=6.0046214850517935e-33)
human1-human2 = KendalltauResult(correlation=0.21302813856969868, pvalue=4.636054486658558e-34)



In [424]:
ROC(male, 'male')
ROC(female, 'female')

clip-vgg = KendalltauResult(correlation=0.2971897043077798, pvalue=3.1614518020119973e-106)
 human-vgg = KendalltauResult(correlation=0.2969645036068334, pvalue=6.146377769255916e-81)
 CLIP_human_ktau = KendalltauResult(correlation=0.25188816692803223, pvalue=9.446202007489692e-59)


clip-vgg = KendalltauResult(correlation=0.2010806523210374, pvalue=3.0148805600873995e-48)
 human-vgg = KendalltauResult(correlation=0.3153841938906672, pvalue=1.648973498420088e-89)
 CLIP_human_ktau = KendalltauResult(correlation=0.2041954979524025, pvalue=1.4333626876800427e-38)


In [416]:
def ROC(df: pd.DataFrame, gender: str):
    CLIP_vgg_ktau = kendalltau(df['CLIP'], df['vgg16'])
    human_vgg_ktau = kendalltau(df['human_dist'], df['vgg16'])
    CLIP_human_ktau = kendalltau(df['human_dist'], df['CLIP'])

    title = f'clip-vgg = {CLIP_vgg_ktau}\n human-vgg = {human_vgg_ktau}\n CLIP_human_ktau = {CLIP_human_ktau}'
    fig = go.Figure()
    fig.add_shape(
        type='line', line=dict(dash='dash'),
        x0=0, x1=1, y0=0, y1=1
    )

    fpr, tpr, thresh, roc_auc = calc_graph_measurements(df, 'isSame', 'human_dist')

    name = f"Human equivalent (AUC={roc_auc:.2f})"
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines'))

    fpr, tpr, thresh, roc_auc = calc_graph_measurements(df, 'isSame', 'CLIP')

    name = f"CLIP (AUC={roc_auc:.2f})"
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines'))

    fpr, tpr, thresh, roc_auc = calc_graph_measurements(df, 'isSame', 'vgg16')

    name = f"vgg16 (AUC={roc_auc:.2f})"
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=name, mode='lines'))


    fig.update_layout(
        title=gender,
        xaxis_title='False Positive Rate',
        yaxis_title='True Positive Rate',
        yaxis=dict(scaleanchor="x", scaleratio=1),
        xaxis=dict(constrain='domain'),
        width=700, height=500
    )
    fig.show()
    fig.write_html(f'/home/administrator/Downloads/{gender}_vgg-clip-human_roc.html')
    print(title)

RT        img_1        img_2  isSame  keyPressed     subject.id  \
179    28522   FM_(3).jpg  SA_(25).jpg       0           1     עידו ארבל    
215    25735  GC_(28).jpg  LW_(18).jpg       0           1     עידו ארבל    
226    24683  FM_(11).jpg  FM_(15).jpg       1           5        הילה מן   
290    21084  CL_(18).jpg  SA_(32).jpg       0           1  יואב יוסף נגל   
296    20852  CL_(29).jpg   CL_(9).jpg       1           6        הילה מן   
...      ...          ...          ...     ...         ...            ...   
27445    957  GC_(34).jpg  LW_(24).jpg       0           1  יואב יוסף נגל   
27463    948   FM_(8).jpg  GC_(30).jpg       0           1  יואב יוסף נגל   
27540    904  FM_(32).jpg  LW_(27).jpg       0           1  יואב יוסף נגל   
27620    854  FM_(32).jpg  GC_(20).jpg       0           1  יואב יוסף נגל   
27640    842  CL_(18).jpg  FM_(25).jpg       0           1      תמרה קפלן   

         age  gender  handedness  sub.mean   sub.std  norm.score  RT>10ms  \
179    s  no     NaN         NaN  1.886003  1.860966   -0.476098        1   
215    s  no     NaN         NaN  1.886003  1.860966   -0.476098        1   
226    s  no     NaN         NaN  1.736311  1.595538    2.045510        1   
290    s  no     NaN         NaN  2.000000  1.824426   -0.548118        1   
296    s  no     NaN         NaN  1.736311  1.595538    2.672257        1   
...      ...     ...         ...       ...       ...         ...      ...   
27445  s  no     NaN         NaN  2.000000  1.824426   -0.548118        0   
27463  s  no     NaN         NaN  2.000000  1.824426   -0.548118        0   
27540  s  no     NaN         NaN  2.000000  1.824426   -0.548118        0   
27620  s  no     NaN         NaN  2.000000  1.824426   -0.548118        0   
27640  s  no     NaN         NaN  2.188761  1.395894   -0.851613        0   

       human_dist      CLIP      vgg16  
179             5  0.769780  243.36821  
215             5  0.697626  194.01228  
226             1  0.662919  167.82613  
290             5  0.874765  123.87965  
296             0  0.499776  128.65181  
...           ...       ...        ...  
27445           5  0.789928  245.13055  
27463           5  0.971626  232.30130  
27540           5  0.919791  258.20688  
27620           5  0.904171  276.62723  
27640           5  0.809423  228.92516  

[2415 rows x 16 columns]

In [608]:
def human_correlation_hist(data: pd.DataFrame, participants: pd.DataFrame, gender: str, alpha: float = 0.05, count: int = 1000):
    correlations = []
    i = 0
    while i < count:
        df = sample_human_equivalent_participant(data, participants, gender)
        ktau = kendalltau(df['human1_dist'], df['human2_dist'])
        if ktau.pvalue < alpha:
            i+=1
            correlations.append(ktau.correlation)
        
    return correlations

In [ ]:
def nn_correlation_hist(data: pd.DataFrame, participants: pd.DataFrame, gender: str, alpha: float = 0.05, count: int = 1000):
    correlations = []
    i = 0
    while i < count:
        df = sample_human_equivalent_participant(data, participants, gender)
        ktau = kendalltau(df['human1_dist'], df['human2_dist'])
        if ktau.pvalue < alpha:
            i+=1
            correlations.append(ktau.correlation)
        
    return correlations

In [609]:
fig = make_subplots(
    rows=1, cols=1, shared_xaxes=True, 
    vertical_spacing=0.02,
    # column_widths=3*[250], row_heights=2*[100], 
    column_titles=['between human k-tau correlations'])
participants_path = '/home/administrator/datasets/itays_exp_human_measurements/participants.csv'
participants_data_path = '/home/administrator/datasets/itays_exp_human_measurements/males_raw_data.csv'

participants = pd.read_csv(participants_path)
data = pd.read_csv(participants_data_path)
male_correlations = human_correlation_hist(data, participants, 'm')

print(male_correlations)
male_mean = sum(male_correlations)/len(male_correlations)

fig.add_trace(go.Histogram(x=male_correlations, name=f'male k-tau (mean={male_mean})'), row=1, col=1)

participants_path = '/home/administrator/datasets/itays_exp_human_measurements/participants.csv'
participants_data_path = '/home/administrator/datasets/itays_exp_human_measurements/females_raw_data.csv'

participants = pd.read_csv(participants_path)
data = pd.read_csv(participants_data_path)
female_correlations = human_correlation_hist(data, participants, 'f')

female_mean = sum(female_correlations)/len(female_correlations)

fig.add_trace(go.Histogram(x=female_correlations, name=f'female k-tau (mean={female_mean})'), row=1, col=1)

fig.show()

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is tryin

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is tryin

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is tryin

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is tryin

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is tryin

...

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is tryin

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is tryin

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is tryin

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is tryin

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is tryin

In [610]:
fig.update_layout(barmode='overlay')
# Reduce opacity to see both histograms
fig.update_traces(opacity=0.75)
fig.show()

In [611]:
fig.write_html('/home/ssd_storage/experiments/CLIP-vgg-Human comparison/human_k-tau_hist.html')

In [665]:
from tqdm import tqdm

def mean(lst: list):
    return sum(lst) / len(lst)



count = 1000
# nn1_path='/home/administrator/Downloads/female_l2_not_normed_images_distance_matrix_2021_10_05_12_07_38_219932.csv'
nn1_path='/home/administrator/Downloads/female_rn50x16_images_distance_matrix_2021_10_07_13_07_12_087880.csv'
nn2_path='/home/administrator/experiments/high_importance_features_full_dataset/vgg16/results/female/fc7.csv'
participants_path = '/home/administrator/datasets/itays_exp_human_measurements/participants.csv'
participants_data_path = '/home/administrator/datasets/itays_exp_human_measurements/females_raw_data.csv'

male_clip_corr = []
male_vgg_corr = []
male_human_corr = []
female_clip_corr = []
female_vgg_corr = []
female_human_corr = []

correlate = pearsonr # kendalltau
correlate_label = 'pearson r' # 'k-tau'

for i in tqdm(range(count)):
    joined = load_all_data(nn1_path, 'CLIP', nn2_path, 'vgg16', participants_path, participants_data_path, 'f')
    
    human_vgg_ktau = correlate(joined['human1_dist'], joined['vgg16'])
#     if human_vgg_ktau.pvalue < 0.05:
#         female_vgg_corr.append(human_vgg_ktau.correlation)
    if human_vgg_ktau[1] < 0.05:
        female_vgg_corr.append(human_vgg_ktau[0])
        
    CLIP_human_ktau = correlate(joined['human1_dist'], joined['CLIP'])
    if CLIP_human_ktau[1] < 0.05:
        female_clip_corr.append(CLIP_human_ktau[0])
#     if CLIP_human_ktau.pvalue < 0.05:
#         female_clip_corr.append(CLIP_human_ktau.correlation)
    
    human_human_ktau = correlate(joined['human1_dist'], joined['human2_dist'])
    if human_human_ktau[1] < 0.05:
        female_human_corr.append(human_human_ktau[0])
#     if human_human_ktau.pvalue < 0.05:
#         female_human_corr.append(human_human_ktau.correlation)
    
# nn1_path='/home/administrator/Downloads/male_l2_not_normed_images_distance_matrix_2021_10_05_12_09_07_849568.csv'
nn1_path='/home/administrator/Downloads/male_rn50x16_images_distance_matrix_2021_10_07_13_09_24_712292.csv'
nn2_path='/home/administrator/experiments/high_importance_features_full_dataset/vgg16/results/male/fc7.csv'
participants_path = '/home/administrator/datasets/itays_exp_human_measurements/participants.csv'
participants_data_path = '/home/administrator/datasets/itays_exp_human_measurements/males_raw_data.csv'

for i in tqdm(range(count)):
    joined = load_all_data(nn1_path, 'CLIP', nn2_path, 'vgg16', participants_path, participants_data_path, 'm')
    
    human_vgg_ktau = correlate(joined['human1_dist'], joined['vgg16'])
    male_vgg_corr.append(human_vgg_ktau[0])
#     if human_vgg_ktau.pvalue < 0.05:
#         male_vgg_corr.append(human_vgg_ktau.correlation)
        
    CLIP_human_ktau = correlate(joined['human1_dist'], joined['CLIP'])
    male_clip_corr.append(CLIP_human_ktau[0])
#     if CLIP_human_ktau.pvalue < 0.05:
#         male_clip_corr.append(CLIP_human_ktau.correlation)

    human_human_ktau = correlate(joined['human1_dist'], joined['human2_dist'])
    male_human_corr.append(human_human_ktau[0])
#     if human_human_ktau.pvalue < 0.05:
#         male_human_corr.append(human_human_ktau.correlation)



  0%|          | 0/1000 [00:00<?, ?it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  0%|          | 1/1000 [00:00<07:04,  2.35it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.

  1%|          | 10/1000 [00:04<07:05,  2.33it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  1%|          | 11/1000 [00:04<07:06,  2.32it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/li

  2%|▏         | 20/1000 [00:08<06:43,  2.43it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  2%|▏         | 21/1000 [00:08<06:42,  2.43it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/li

  3%|▎         | 30/1000 [00:12<06:44,  2.40it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  3%|▎         | 31/1000 [00:12<06:40,  2.42it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/li

  4%|▍         | 40/1000 [00:16<06:34,  2.44it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  4%|▍         | 41/1000 [00:17<06:33,  2.44it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/li

...

 96%|█████████▌| 960/1000 [06:29<00:16,  2.47it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

 96%|█████████▌| 961/1000 [06:29<00:16,  2.30it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/

 97%|█████████▋| 970/1000 [06:33<00:12,  2.50it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

 97%|█████████▋| 971/1000 [06:34<00:11,  2.50it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/

 98%|█████████▊| 980/1000 [06:37<00:08,  2.39it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

 98%|█████████▊| 981/1000 [06:38<00:07,  2.39it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/

 99%|█████████▉| 990/1000 [06:41<00:03,  2.50it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1596: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/home/administrator/anaconda3/envs/facial_feature_impact_comparison/lib/python3.8/site-packages/pandas/core/indexing.py:1745: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

 99%|█████████▉| 991/1000 [06:42<00:03,  2.50it/s]/home/administrator/anaconda3/envs/facial_feature_impact_comparison/

100%|██████████| 1000/1000 [06:45<00:00,  2.46it/s]


In [668]:
print(len(female_clip_corr))
print(len(female_vgg_corr))
print(len(male_clip_corr))
print(len(male_vgg_corr))
print(len(male_human_corr))
print(len(female_human_corr))


fig = make_subplots(
    rows=1, cols=2, shared_xaxes=True, 
    vertical_spacing=0.02,
    # column_widths=3*[250], row_heights=2*[100], 
    column_titles=[f'female {correlate_label} correlations', f'male {correlate_label} correlations'])

fig.add_trace(go.Histogram(x=female_human_corr, name=f'human {correlate_label} (mean={mean(female_human_corr)}, n={len(female_human_corr)})', marker_color=px.colors.qualitative.Plotly[0]), row=1, col=1)
fig.add_trace(go.Histogram(x=female_clip_corr, name=f'CLIP {correlate_label} (mean={mean(female_clip_corr)}, n={len(female_clip_corr)})', marker_color=px.colors.qualitative.Plotly[1]), row=1, col=1)
fig.add_trace(go.Histogram(x=female_vgg_corr, name=f'vgg {correlate_label} (mean={mean(female_vgg_corr)}, n={len(female_vgg_corr)})', marker_color=px.colors.qualitative.Plotly[2]), row=1, col=1)


fig.add_trace(go.Histogram(x=male_human_corr, name=f'human {correlate_label} (mean={mean(male_human_corr)}, n={len(male_human_corr)})', marker_color=px.colors.qualitative.Plotly[0]), row=1, col=2)
fig.add_trace(go.Histogram(x=male_clip_corr, name=f'CLIP {correlate_label} (mean={mean(male_clip_corr)}, n={len(male_clip_corr)})', marker_color=px.colors.qualitative.Plotly[1]), row=1, col=2)
fig.add_trace(go.Histogram(x=male_vgg_corr, name=f'vgg {correlate_label} (mean={mean(male_vgg_corr)}, n={len(male_vgg_corr)})', marker_color=px.colors.qualitative.Plotly[2]), row=1, col=2)


fig.update_layout(barmode='overlay')
# Reduce opacity to see both histograms
fig.update_traces(opacity=0.75)
fig.update_layout(height=600, width=1500)
fig.show()

1000
1000
1000
1000
1000
1000


In [669]:
fig.write_html('/home/ssd_storage/experiments/CLIP-vgg-Human comparison/rn50x16-all_pearson-r_hists.html')